In [1]:
import math
from datetime import datetime, timedelta
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split, GridSearchCV, cross_val_score
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, StackingClassifier
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score, confusion_matrix, roc_auc_score
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline

In [2]:
url = 'https://raw.githubusercontent.com/JeffSackmann/tennis_MatchChartingProject/master/charting-m-points-2010s.csv'

columns_with_mixed_types = [8, 9, 29]

# Define column types for columns with mixed data types and read the csv
dtype_dict = {col: str for col in columns_with_mixed_types}
m_2010s = pd.read_csv(url, encoding='latin1', dtype=dtype_dict)

In [3]:
print(m_2010s.columns)
m_2010s

Index(['match_id', 'Pt', 'Set1', 'Set2', 'Gm1', 'Gm2', 'Pts', 'Gm#', 'TbSet',
       'TB?', 'TBpt', 'Svr', 'Ret', 'Serving', '1st', '2nd', 'Notes', '1stSV',
       '2ndSV', '1stIn', '2ndIn', 'isAce', 'isUnret', 'isRallyWinner',
       'isForced', 'isUnforced', 'isDouble', 'PtWinner', 'isSvrWinner',
       'rallyCount'],
      dtype='object')


match_id   Pt  Set1  Set2  \
0       20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...    1     0     0   
1       20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...    2     0     0   
2       20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...    3     0     0   
3       20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...    4     0     0   
4       20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...    5     0     0   
...                                                   ...  ...   ...   ...   
305154  20100108-M-Doha-SF-Roger_Federer-Nikolay_Davyd...  119     0     1   
305155  20100108-M-Doha-SF-Roger_Federer-Nikolay_Davyd...  120     0     1   
305156  20100108-M-Doha-SF-Roger_Federer-Nikolay_Davyd...  121     0     1   
305157  20100108-M-Doha-SF-Roger_Federer-Nikolay_Davyd...  122     0     1   
305158  20100108-M-Doha-SF-Roger_Federer-Nikolay_Davyd...  123     0     1   

        Gm1  Gm2    Pts    Gm# TbSet TB?  ...  2ndIn  isAce  isUnret  \
0         0  0.0    0-0  1 (1)     1   0  ...    1.0  False    False   
1         0  0.0   15-0  1 (2)     1   0  ...    1.0  False    False   
2         0  0.0   30-0  1 (3)     1   0  ...    NaN  False    False   
3         0  0.0   40-0  1 (4)     1   0  ...    NaN  False    False   
4         1  0.0    0-0  2 (1)     1   0  ...    1.0  False    False   
...     ...  ...    ...    ...   ...  ..  ...    ...    ...      ...   
305154    3  5.0  AD-40     19     1   0  ...    1.0  False    False   
305155    4  5.0    0-0     20     1   0  ...    1.0  False    False   
305156    4  5.0   15-0     20     1   0  ...    NaN  False    False   
305157    4  5.0   30-0     20     1   0  ...    NaN  False    False   
305158    4  5.0   40-0     20     1   0  ...    NaN  False    False   

       isRallyWinner isForced isUnforced isDouble  PtWinner  isSvrWinner  \
0              False    False       True    False         1            1   
1              False    False       True    False         1            1   
2              False    False      False    False         1            1   
3              False     True      False    False         1            1   
4              False    False       True    False         1            0   
...              ...      ...        ...      ...       ...          ...   
305154         False     True      False    False         1            1   
305155         False     True      False    False         2            1   
305156         False    False       True    False         2            1   
305157          True    False      False    False         2            1   
305158         False     True      False    False         2            1   

        rallyCount  
0                3  
1                7  
2                1  
3                1  
4                2  
...            ...  
305154           1  
305155           1  
305156          11  
305157          11  
305158           1  

[305159 rows x 30 columns]

In [4]:
print(m_2010s['Set1'].unique())
print(m_2010s['Gm1'].unique())
print(m_2010s['rallyCount'].unique())


filtered_m_2010s = m_2010s[(m_2010s['Gm1'] > 6) | (m_2010s['Gm2'] > 6)]
print("Rows where 'Gm1' or 'Gm2' is greater than 6:")
print(filtered_m_2010s)

filtered_match_ids = filtered_m_2010s['match_id'].unique()
m_2010s = m_2010s[~m_2010s['match_id'].isin(filtered_match_ids)]

filtered_m_2010s = m_2010s[(m_2010s['Gm1'] > 6) | (m_2010s['Gm2'] > 6)]
print("Rows where 'Gm1' or 'Gm2' is greater than 6:")
print(filtered_m_2010s)

[0 1 2]
[ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68]
['3' '7' '1' '2' '6' '5' '4' '8' '12' '0' '11' '9' '10' '14' '13' '21'
 '17' '15' '20' '16' '18' '24' '23' '19' '30' '35' '22' '37' '32' '39'
 '34' '33' '26' '31' '28' '25' '44' '42' '27' '29' '45' '40' '38' '36'
 '43' '46' '84' '47' '41' '54' nan '#NAME?']
Rows where 'Gm1' or 'Gm2' is greater than 6:
                                                 match_id   Pt  Set1  Set2  \
30465   20190714-M-Wimbledon-F-Roger_Federer-Novak_Djo...  344     2     2   
30466   20190714-M-Wimbledon-F-Roger_Federer-Novak_Djo...  345     2     2   
30467   20190714-M-Wimbledon-F-Roger_Federer-Novak_Djo...  346     2     2   
30468   20190714-M-Wimbledon-F-Roger_Federer-Novak_Djo...  347     2     2   
30469   20190714-M-Wimbledon-F-Roger_Federer-Novak_Djo...  348     2     2   
...       

In [5]:
m_2010s.rename(columns={'Gm1':'p1_games','Gm2':'p2_games',
                        'Set1':'p1_sets','Set2':'p2_sets',
                        'Pt':'point_no','rallyCount':'rally_count',
                        'Svr':'server','PtWinner':'point_victor'}, inplace=True)

m_2010s[['p1_score', 'p2_score']] = m_2010s['Pts'].str.split('-', expand=True)

def mean_imputation(dataframe_column):
    mean_value = dataframe_column.mean(skipna=True)
    dataframe_column.fillna(mean_value, inplace=True)
    return dataframe_column

def replace_column_value(df, column_name, old_value, new_value):
    df[column_name] = df[column_name].replace(old_value, new_value)
    return df

m_2010s['rally_count'] = pd.to_numeric(m_2010s['rally_count'], errors='coerce')
m_2010s['rally_count'] = mean_imputation(m_2010s['rally_count'])
m_2010s = replace_column_value(m_2010s,"p1_score","AD",45)
m_2010s = replace_column_value(m_2010s,"p2_score","AD",45)

m_2010s.loc[:,'estimated_time'] = m_2010s.loc[:,'point_no']*m_2010s.loc[:,'rally_count']

C:\Users\zhuzi\AppData\Local\Temp\ipykernel_12920\1038455794.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  m_2010s.rename(columns={'Gm1':'p1_games','Gm2':'p2_games',
C:\Users\zhuzi\AppData\Local\Temp\ipykernel_12920\1038455794.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  m_2010s[['p1_score', 'p2_score']] = m_2010s['Pts'].str.split('-', expand=True)
C:\Users\zhuzi\AppData\Local\Temp\ipykernel_12920\1038455794.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = valu

In [6]:
m_2010s_dfs = {}
for match_id in m_2010s['match_id'].unique():
    match_df = m_2010s[m_2010s['match_id'] == match_id].copy()
    
    match_df['p1_points_won'] = 0
    match_df['p2_points_won'] = 0
    match_df.loc[match_df['point_victor'] == 1, 'p1_points_won'] += 1
    match_df.loc[match_df['point_victor'] == 2, 'p2_points_won'] += 1
    match_df.loc[:,'cumulative_points_diff'] = match_df.loc[:,'p1_points_won']-match_df.loc[:,'p2_points_won']
    
    match_df['p1_consistency'] = match_df['point_victor'].rolling(window=3, min_periods=1).apply(lambda x: (x == 1).sum(), raw=True)
    match_df['p2_consistency'] = match_df['point_victor'].rolling(window=3, min_periods=1).apply(lambda x: (x == 2).sum(), raw=True)
    
    match_df.loc[match_df.index < 3, ['p1_consistency', 'p2_consistency']] = 0
    
    match_df['point_victor_result'] = match_df['point_victor'].shift(-1)
    match_df['point_victor_result'].fillna(method='ffill', inplace=True)
    
    match_df['game_no'] = 1
    match_df['set_no'] = 1
    match_df['game_victor'] = 0

    prev_p1_games = match_df.iloc[0]['p1_games']
    prev_p2_games = match_df.iloc[0]['p2_games']
    prev_p1_sets = match_df.iloc[0]['p1_sets']
    prev_p2_sets = match_df.iloc[0]['p2_sets']


    for idx, row in match_df.iterrows():
        if (row['p1_games'] != prev_p1_games) or (row['p2_games'] != prev_p2_games):
            match_df.at[idx, 'game_no'] = match_df.at[idx - 1, 'game_no'] + 1

        if (row['p1_sets'] != prev_p1_sets) or (row['p2_sets'] != prev_p2_sets):
            match_df.at[idx, 'set_no'] = match_df.at[idx - 1, 'set_no'] + 1

        if row['p1_games'] != prev_p1_games:
            match_df.at[idx, 'game_victor'] = 1
        elif row['p2_games'] != prev_p2_games:
            match_df.at[idx, 'game_victor'] = 2

        prev_p1_games = row['p1_games']
        prev_p2_games = row['p2_games']
        prev_p1_sets = row['p1_sets']
        prev_p2_sets = row['p2_sets']
    
    m_2010s_dfs[match_id] = match_df
m_2010s_dfs

{'20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Denis_Shapovalov':                                               match_id  point_no  p1_sets  \
 0    20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...         1        0   
 1    20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...         2        0   
 2    20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...         3        0   
 3    20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...         4        0   
 4    20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...         5        0   
 ..                                                 ...       ...      ...   
 145  20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...       146        1   
 146  20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...       147        1   
 147  20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...       148        1   
 148  20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...       149        1   
 149  20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Den...       150        1   
 

In [10]:
print(m_2010s_dfs['20191124-M-Davis_Cup_Finals-F-Rafael_Nadal-Denis_Shapovalov'].columns)
m_2010s_modified = pd.concat(m_2010s_dfs.values(), ignore_index=True)
m_2010s_modified.isna().values.any()

Index(['match_id', 'point_no', 'p1_sets', 'p2_sets', 'p1_games', 'p2_games',
       'Pts', 'Gm#', 'TbSet', 'TB?', 'TBpt', 'server', 'Ret', 'Serving', '1st',
       '2nd', 'Notes', '1stSV', '2ndSV', '1stIn', '2ndIn', 'isAce', 'isUnret',
       'isRallyWinner', 'isForced', 'isUnforced', 'isDouble', 'point_victor',
       'isSvrWinner', 'rally_count', 'p1_score', 'p2_score', 'estimated_time',
       'p1_points_won', 'p2_points_won', 'cumulative_points_diff',
       'p1_consistency', 'p2_consistency', 'point_victor_result', 'game_no',
       'set_no', 'game_victor'],
      dtype='object')


True

In [8]:
m_2010s_modified.to_pickle('m_2010s_modified.pkl')